Reference paper: stability is stable 
Experiment: vary the value of rho and see the minimum sample size required for replicability

func getConvergenceSampleNum(hyperparams)
    For sample_num range(min_subsets_size, max_subsets_size, step):
        For range(repeat_num):
            random draw a subset of the dataset, whose size = sample_num
            Use algorithm 10 to get a model
        Check whether the models we get are 'replicable' to each other, accoding to the hyperparams. (see definition in page 14 of the paper)
        if converged, return current sample_num

func experiment(): 
# vary the rho and see minumum sample size required for replicability. 
# To make it simple, we can fix the value of other hyperparamers, such as alpha and beta.
    for rho in range(min_rho, max_rho, step):
        sample_num = getConvergenceSampleNum(rho)
        theoretical_sample_num = getTheoreticalSampleNum(rho) # compute according to algorithm 10 in the paper
        print("Hyperparams: ", hyperparams, "Sample size: ", sample_num)
    plot(hyperparams, theoretical_sample_num) # draw the curve, where x-axis is the hyperparams and y-axis is the sample size
    plot(hyperparams, sample_num) # draw the curve, where x-axis is the hyperparams and y-axis is the sample size

In [6]:
import pandas as pd
import numpy as np
import config
import Algorithm10 as a10
from sklearn.tree import export_text

In [7]:
data = pd.read_csv('dataset/Invistico_Airline.csv')
data.head()

satisfaction   Customer Type  Age   Type of Travel     Class  \
0    satisfied  Loyal Customer   65  Personal Travel       Eco   
1    satisfied  Loyal Customer   47  Personal Travel  Business   
2    satisfied  Loyal Customer   15  Personal Travel       Eco   
3    satisfied  Loyal Customer   60  Personal Travel       Eco   
4    satisfied  Loyal Customer   70  Personal Travel       Eco   

   Flight Distance  Seat comfort  Departure/Arrival time convenient  \
0              265             0                                  0   
1             2464             0                                  0   
2             2138             0                                  0   
3              623             0                                  0   
4              354             0                                  0   

   Food and drink  Gate location  ...  Online support  Ease of Online booking  \
0               0              2  ...               2                       3   
1               0              3  ...               2                       3   
2               0              3  ...               2                       2   
3               0              3  ...               3                       1   
4               0              3  ...               4                       2   

   On-board service  Leg room service  Baggage handling  Checkin service  \
0                 3                 0                 3                5   
1                 4                 4                 4                2   
2                 3                 3                 4                4   
3                 1                 0                 1                4   
4                 2                 0                 2                4   

   Cleanliness  Online boarding  Departure Delay in Minutes  \
0            3                2                           0   
1            3                2                         310   
2            4                2                           0   
3            1                3                           0   
4            2                5                           0   

   Arrival Delay in Minutes  
0                       0.0  
1                     305.0  
2                       0.0  
3                       0.0  
4                       0.0  

[5 rows x 22 columns]

In [8]:
data.shape

(129880, 22)

In [ ]:
def are_trees_equal(tree1, tree2):
    # Check that both trees are fitted
    if not hasattr(tree1, 'tree_') or not hasattr(tree2, 'tree_'):
        raise ValueError("Both trees must be fitted before comparison.")

    # Compare parameters
    if tree1.get_params() != tree2.get_params():
        return False

    t1 = tree1.tree_
    t2 = tree2.tree_

    # Compare structure and splitting rules
    attributes_to_check = [
        'children_left', 'children_right',
        'feature', 'threshold',
        'impurity', 'n_node_samples', 'weighted_n_node_samples',
        'value'
    ]

    for attr in attributes_to_check:
        if not np.array_equal(getattr(t1, attr), getattr(t2, attr)):
            return False

    return True

In [16]:
X, y = a10.load_full_dataset(config.dataset_path, random_state=config.random_seed)
H = a10.build_candidate_trees(X, y,sample_size = 100000, max_depth=config.max_depth, num_trees=config.num_H, random_state=config.random_seed)    

for sample_size in range(10000, 20000 + 1, 500):
    qualifying_trees_list = []
    for i in range(2):
        res_trees = a10.replicable_learner(X, y, H, sample_size=sample_size, random_seed=config.random_seed+i)
        qualifying_trees_list.append(res_trees)
    #compare the percentage of tree that are equal in the two lists
    equal_trees = 0
    print("\nSample size: ", sample_size)
    print("Number of trees in the first list: ", len(qualifying_trees_list[0]))
    print("Number of trees in the second list: ", len(qualifying_trees_list[1]))
    smaller_list = min(len(qualifying_trees_list[0]), len(qualifying_trees_list[1]))
    for i in range(len(qualifying_trees_list[0])):
        for j in range(len(qualifying_trees_list[1])):
            if are_trees_equal(qualifying_trees_list[0][i], qualifying_trees_list[1][j]):
                equal_trees += 1
                continue
    print("Number of equal trees: ", equal_trees)

100%|██████████| 10/10 [00:00<00:00, 16.71it/s]


OPT error 0.24080000000000001 errors dict_values([0.24080000000000001, 0.24080000000000001, 0.24080000000000001, 0.24080000000000001, 0.24080000000000001, 0.24080000000000001, 0.24080000000000001, 0.24080000000000001, 0.24080000000000001, 0.24080000000000001])
k: 18 v max candidates: 0.26384445136022094 v min candidates: 0.2416954327831551
[np.float64(0.2416954327831551), np.float64(0.24299831622886486), np.float64(0.24430119967457462), np.float64(0.24560408312028437), np.float64(0.24690696656599412), np.float64(0.24820985001170387), np.float64(0.24951273345741362), np.float64(0.2508156169031234), np.float64(0.25211850034883315), np.float64(0.2534213837945429), np.float64(0.25472426724025266), np.float64(0.25602715068596243), np.float64(0.25733003413167216), np.float64(0.25863291757738194), np.float64(0.25993580102309166), np.float64(0.26123868446880144), np.float64(0.26254156791451116), np.float64(0.26384445136022094)]
v: 0.24560408312028437
OPT error 0.23440000000000005 errors dict_v

In [21]:
def getConvergenceSampleNum(min_subset_size, max_subset_size, repeat_num, rho, sample_size_step=1):
    sample_size_replicablity_dict = {}
    
    X, y= a10.load_full_dataset(config.dataset_path, random_state=config.random_seed)
    for sample_size in range(min_subset_size, max_subset_size + 1, sample_size_step):
        #get dataset of size sample_size by sampling from the original dataset
        replicable_tree_list = []
        H = a10.build_candidate_trees(X, y,sample_size, max_depth=config.max_depth, num_trees=config.num_H, random_state=config.random_seed)    
        for i in range(repeat_num):
            print(f"sample size: {sample_size}, repeat: {i}")
            res_trees = a10.replicable_learner(X, y, H, sample_size, random_seed=config.random_seed+i)
            print(f"number of res_trees: {len(res_trees)}")
            # check whether the candidate trees below v are same to each other
            for a in range(len(res_trees)):
                for b in range(a + 1, len(res_trees)):
                    if are_trees_equal(res_trees[a], res_trees[b]):
                        print(f"tree {a} and tree {b} are the same")
                    else:
                        print(f"tree {a} and tree {b} are different")
                        print("tree a",export_text(res_trees[a]),"tree b",export_text(res_trees[b]))
            tree = res_trees[0]
            replicable_tree_list.append(tree)
            
        #check the probability if the trees in the replicable_tree_list are the same
        same_tree_count = 0
        for i in range(len(replicable_tree_list)):
            for j in range(i + 1, len(replicable_tree_list)):
                
                if are_trees_equal(replicable_tree_list[i], replicable_tree_list[j]):
                    # print(f"tree {i} and tree {j} are the same")
                    same_tree_count += 1
        prob = same_tree_count / (repeat_num * (repeat_num - 1) / 2)
        sample_size_replicablity_dict[sample_size] = prob
        # if prob >= 1-rho:
        #     print(f"replicable at sample size: {sample_size}, prob: {prob}")
        #     return sample_size 
    return sample_size_replicablity_dict
        
    # # return sample_size_replicablity_dict
    # print(f"not replicable at sample size between {min_subset_size} and {max_subset_size}, prob: {prob}")
    # return -1

            
        
    

In [24]:
print("theoretical sample size: ", config.m_up_bound)
ans_dict = getConvergenceSampleNum(min_subset_size=10000, max_subset_size=20000, repeat_num=10, rho=config.rho, sample_size_step=500)
# print("sample size replicability dict: ", ans_dict)

theoretical sample size:  81365.1085764509


100%|██████████| 10/10 [00:00<00:00, 44.23it/s]


sample size: 10000, repeat: 0
OPT error 0.21919999999999995 errors dict_values([0.24080000000000001, 0.24080000000000001, 0.24080000000000001, 0.24080000000000001, 0.24080000000000001, 0.23399999999999999, 0.21919999999999995, 0.21919999999999995, 0.21919999999999995, 0.21919999999999995])
k: 18 v max candidates: 0.24224445136022088 v min candidates: 0.22009543278315505
[np.float64(0.22009543278315505), np.float64(0.2213983162288648), np.float64(0.22270119967457455), np.float64(0.2240040831202843), np.float64(0.22530696656599405), np.float64(0.2266098500117038), np.float64(0.22791273345741356), np.float64(0.22921561690312334), np.float64(0.2305185003488331), np.float64(0.23182138379454284), np.float64(0.2331242672402526), np.float64(0.23442715068596234), np.float64(0.2357300341316721), np.float64(0.23703291757738185), np.float64(0.2383358010230916), np.float64(0.23963868446880138), np.float64(0.24094156791451113), np.float64(0.24224445136022088)]
v: 0.2240040831202843
number of res_tre

100%|██████████| 10/10 [00:00<00:00, 38.02it/s]


sample size: 10500, repeat: 0
OPT error 0.21857142857142853 errors dict_values([0.24076190476190473, 0.24076190476190473, 0.24076190476190473, 0.24076190476190473, 0.24076190476190473, 0.24076190476190473, 0.21857142857142853, 0.21857142857142853, 0.21857142857142853, 0.21857142857142853])
k: 18 v max candidates: 0.24161587993164946 v min candidates: 0.21946686135458363
[np.float64(0.21946686135458363), np.float64(0.22076974480029338), np.float64(0.22207262824600313), np.float64(0.22337551169171288), np.float64(0.22467839513742263), np.float64(0.22598127858313238), np.float64(0.22728416202884213), np.float64(0.22858704547455191), np.float64(0.22988992892026167), np.float64(0.23119281236597142), np.float64(0.23249569581168117), np.float64(0.23379857925739092), np.float64(0.23510146270310067), np.float64(0.23640434614881042), np.float64(0.23770722959452018), np.float64(0.23901011304022995), np.float64(0.2403129964859397), np.float64(0.24161587993164946)]
v: 0.22337551169171288
number of 

...

sample size: 19000, repeat: 0
OPT error 0.21505263157894738 errors dict_values([0.23863157894736842, 0.23863157894736842, 0.23863157894736842, 0.23863157894736842, 0.23863157894736842, 0.23863157894736842, 0.21505263157894738, 0.21505263157894738, 0.23863157894736842, 0.21505263157894738])
k: 18 v max candidates: 0.23809708293916831 v min candidates: 0.21594806436210248
[np.float64(0.21594806436210248), np.float64(0.21725094780781223), np.float64(0.21855383125352199), np.float64(0.21985671469923174), np.float64(0.2211595981449415), np.float64(0.22246248159065124), np.float64(0.223765365036361), np.float64(0.22506824848207077), np.float64(0.22637113192778052), np.float64(0.22767401537349027), np.float64(0.22897689881920003), np.float64(0.23027978226490978), np.float64(0.23158266571061953), np.float64(0.23288554915632928), np.float64(0.23418843260203903), np.float64(0.2354913160477488), np.float64(0.23679419949345856), np.float64(0.23809708293916831)]
v: 0.21985671469923174
number of res

100%|██████████| 10/10 [00:00<00:00, 34.58it/s]


sample size: 19500, repeat: 0
OPT error 0.21476923076923082 errors dict_values([0.23815384615384616, 0.23815384615384616, 0.23815384615384616, 0.23815384615384616, 0.23815384615384616, 0.23815384615384616, 0.21476923076923082, 0.21476923076923082, 0.23815384615384616, 0.21476923076923082])
k: 18 v max candidates: 0.23781368212945175 v min candidates: 0.21566466355238592
[np.float64(0.21566466355238592), np.float64(0.21696754699809567), np.float64(0.21827043044380542), np.float64(0.21957331388951518), np.float64(0.22087619733522493), np.float64(0.22217908078093468), np.float64(0.22348196422664443), np.float64(0.2247848476723542), np.float64(0.22608773111806396), np.float64(0.2273906145637737), np.float64(0.22869349800948346), np.float64(0.22999638145519322), np.float64(0.23129926490090297), np.float64(0.23260214834661272), np.float64(0.23390503179232247), np.float64(0.23520791523803225), np.float64(0.236510798683742), np.float64(0.23781368212945175)]
v: 0.21957331388951518
number of res

100%|██████████| 10/10 [00:00<00:00, 35.83it/s]


sample size: 20000, repeat: 0
OPT error 0.21530000000000005 errors dict_values([0.23885, 0.23885, 0.23885, 0.23885, 0.21530000000000005, 0.23885, 0.21530000000000005, 0.21530000000000005, 0.23885, 0.21530000000000005])
k: 18 v max candidates: 0.23834445136022098 v min candidates: 0.21619543278315514
[np.float64(0.21619543278315514), np.float64(0.2174983162288649), np.float64(0.21880119967457465), np.float64(0.2201040831202844), np.float64(0.22140696656599415), np.float64(0.2227098500117039), np.float64(0.22401273345741365), np.float64(0.22531561690312343), np.float64(0.22661850034883319), np.float64(0.22792138379454294), np.float64(0.2292242672402527), np.float64(0.23052715068596244), np.float64(0.2318300341316722), np.float64(0.23313291757738194), np.float64(0.2344358010230917), np.float64(0.23573868446880147), np.float64(0.23704156791451123), np.float64(0.23834445136022098)]
v: 0.2201040831202844
number of res_trees: 4
tree 0 and tree 1 are different
tree a |--- feature_1 <= 3.50
|  

In [25]:
print(ans_dict)

{10000: 0.17777777777777778, 10500: 0.2222222222222222, 11000: 0.2222222222222222, 11500: 0.2222222222222222, 12000: 0.2222222222222222, 12500: 0.2222222222222222, 13000: 0.2222222222222222, 13500: 0.2222222222222222, 14000: 0.2222222222222222, 14500: 0.2222222222222222, 15000: 0.2222222222222222, 15500: 0.2222222222222222, 16000: 0.2222222222222222, 16500: 0.2222222222222222, 17000: 0.2222222222222222, 17500: 0.3111111111111111, 18000: 0.2222222222222222, 18500: 0.2222222222222222, 19000: 0.35555555555555557, 19500: 0.35555555555555557, 20000: 0.3111111111111111}
